In [8]:
import pandas as pd
import tensorflow_hub as hub
import openai 
import numpy as np
import altair as alt
from openai import OpenAI
from sql_metadata import Parser
import os
from IPython.display import display, Markdown
import ast
import cx_Oracle
import re

from pathlib import Path
import sys
sys.path.append('../')
import json
import requests

In [2]:
prefix = Path.cwd().parent.parent
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)
prefix

PosixPath('/home/skikk/Dokumente/uni/WS2324/MIT/llm-enterprise')

In [22]:
from collections import deque
test = {"A":1}
"A" in test.keys()

True

In [66]:
# Open the file in read mode
with open(str(prefix) + '/data/OpenStack_DB_mysql_TIG.log', 'r') as file:
    # Read the file in chunks
    chunk_size = 2500000  # 1 MB
    test = True
    while test:
        chunk = file.read(chunk_size)
        if not chunk:
            break
        # Process the chunk (e.g., print it)
        print(chunk)
        test = False

/usr/sbin/mysqld, Version: 5.5.63-MariaDB-1~trusty-wsrep (mariadb.org binary distribution, wsrep_25.25.r9949137). started with:
Tcp port: 3306  Unix socket: /var/run/mysqld/mysqld.sock
Time                 Id Command    Argument
		3964677 Query	SELECT 1
		3964677 Query	SELECT services.created_at AS services_created_at, services.updated_at AS services_updated_at, services.deleted_at AS services_deleted_at, services.deleted AS services_deleted, services.id AS services_id, services.host AS services_host, services.`binary` AS services_binary, services.topic AS services_topic, services.report_count AS services_report_count, services.disabled AS services_disabled, services.disabled_reason AS services_disabled_reason, services.last_seen_up AS services_last_seen_up, services.forced_down AS services_forced_down, services.version AS services_version 
FROM services 
WHERE services.deleted = 0 AND services.id = 162 
 LIMIT 1
		3964677 Query	UPDATE services SET updated_at='2024-05-10 15:07:24.40893

In [67]:
a = re.split(r'\n\t\t[0-9]+ Query\t', chunk)

In [68]:
a[2]

'SELECT services.created_at AS services_created_at, services.updated_at AS services_updated_at, services.deleted_at AS services_deleted_at, services.deleted AS services_deleted, services.id AS services_id, services.host AS services_host, services.`binary` AS services_binary, services.topic AS services_topic, services.report_count AS services_report_count, services.disabled AS services_disabled, services.disabled_reason AS services_disabled_reason, services.last_seen_up AS services_last_seen_up, services.forced_down AS services_forced_down, services.version AS services_version \nFROM services \nWHERE services.deleted = 0 AND services.id = 162 \n LIMIT 1'

In [69]:
sum_of_tables = 0
sum_of_joins = 0
num_of_queries = 0
sql = []
for i in range(2, len(a)-1):
    if  not a[i].startswith('COMMIT') and not a[i].startswith('ROLLBACK') and not a[i].startswith('SET') and not a[i].startswith('SELECT 1') and 'SAVEPOINT' not in a[i]:
        try:
            number_of_tables = len(Parser(a[i]).tables)
            number_of_joins = a[i].count("JOIN")
            print(str(i)+ ":"+str(number_of_joins)+":"+str(number_of_tables))
            sum_of_tables += number_of_tables
            sum_of_joins += number_of_joins
            num_of_queries += 1
            sql.append(a[i])
        except Exception as e:
            print(e)

2:0:1
3:0:1
7:0:1
8:0:1
11:0:1
12:0:1
17:0:1
18:0:1
22:0:1
23:0:1
27:6:7
30:0:1
33:12:12
36:11:10
38:3:4
39:11:10
40:3:4
42:0:1
46:3:4
49:9:8
52:9:10
55:2:3
58:1:2
61:12:12
64:0:1
70:3:4
73:0:1
75:0:1
76:0:1
79:0:1
80:0:1
82:0:1
84:0:1
85:0:1


Not supported query type: SHOW VARIABLES LIKE "general_log%"


89:0:1
90:0:1
96:0:1
98:0:1
103:0:1
105:0:1
107:0:1
108:0:1
113:0:1
114:0:1
117:0:1
118:0:1
121:0:1
122:0:1
125:0:1
127:0:1
133:0:1
134:0:1
138:0:1
139:0:1
143:0:1
144:0:1
147:0:1
150:0:1
151:0:1
154:0:1
155:0:1
160:0:1
161:0:1
Not supported query type!
166:0:1
167:0:1
171:0:1
172:0:1
176:7:4
178:0:1
180:0:1
184:0:1
186:0:1
187:0:1
190:0:1
192:3:4
194:2:3
196:0:1
199:0:1
200:0:1
202:0:1
204:0:1
208:0:1
213:2:3
214:0:1
216:6:7
221:2:3
222:0:1
226:0:1
230:0:1
231:2:3
232:0:1
236:12:12
240:2:3
242:9:9
243:0:1
245:2:3
247:11:10
248:3:4
249:0:1
253:3:4
259:9:10
260:1:2
263:2:3
266:1:2
268:0:1
272:0:1
274:12:12
276:0:1
280:0:1
283:0:1
287:0:1
288:0:1
295:0:1
298:0:1
301:0:1
304:0:1
306:0:1
311:0:1
314:0:1
317:0:1
320:0:1
324:0:1
325:0:1
328:0:1
334:0:1
337:0:1
340:0:1
343:0:1
346:0:1
349:0:1
353:0:1
354:0:1
358:2:3
360:0:1
361:0:1
366:4:5
369:0:1
370:0:1
374:0:1
377:0:1
380:0:1
381:0:1
385:0:1
387:0:1
393:0:1
397:0:1
401:0:1
402:0:1
406:3:4
409:0:1
413:0:1
414:0:1
418:0:1
421:6:7
424:0:1
429

Not supported query type: SHOW VARIABLES LIKE "%log%"


4486:1:2
4488:0:1
4491:0:1
4494:0:1
4497:0:1
4500:0:1
4503:0:1
4506:0:1
4509:0:1
4512:0:1
4515:0:1
4518:0:1
4521:0:1
4524:2:3
4527:3:4
4529:0:1
4530:0:1
4535:2:3
4538:0:1
4539:0:1
4543:0:1
4544:0:1
4547:0:1
4550:0:1
4551:0:1
4555:0:1
4556:0:1
4560:0:1
4563:0:1
4568:0:1
4572:0:1
4577:0:1
4581:0:1
4586:0:1
4590:0:1
Not supported query type!
4599:7:4
4602:3:4
4604:12:12
4607:3:4
4608:0:1
4609:0:1
4611:13:12
4617:7:8
4621:0:1
4622:0:1
4631:0:1
4632:0:1
4636:0:1
4639:0:1
4643:0:1
4648:0:1
4649:1:2
4650:2:3
4651:6:7
4652:1:2
4655:0:1
4658:0:1
4661:0:1
4664:0:1
4668:0:1
4671:0:1
4674:0:1
4675:0:1
4678:0:1
4681:0:1
4683:0:1
4685:1:2
4686:2:3
4687:1:2
4688:1:2
4691:0:1
4695:0:1
4700:0:1
4701:0:1
4706:0:1
4707:0:1
4711:0:1
4714:0:1
4717:0:1
4719:0:1
4722:1:2
4723:0:1
4725:2:3
4727:1:2
4728:0:1
4732:0:1
4736:0:1
4737:1:2
4740:0:1
4743:0:1
4747:0:1
4750:0:1
4753:0:1
4757:0:1
4758:0:1
4760:0:1
4763:0:1
4766:0:1
4770:0:1
4771:0:1
4773:1:2
4775:2:3
4776:0:1
4777:1:2
4778:1:2
4780:1:2
4782:0:1
4783:2:

In [70]:
sum_of_tables/num_of_queries

2.6282327586206895

In [71]:
num_of_queries

1856

In [72]:
unique_sql = set(sql)
unique_sql

{"SELECT instance_system_metadata.created_at AS instance_system_metadata_created_at, instance_system_metadata.updated_at AS instance_system_metadata_updated_at, instance_system_metadata.deleted_at AS instance_system_metadata_deleted_at, instance_system_metadata.deleted AS instance_system_metadata_deleted, instance_system_metadata.id AS instance_system_metadata_id, instance_system_metadata.`key` AS instance_system_metadata_key, instance_system_metadata.value AS instance_system_metadata_value, instance_system_metadata.instance_uuid AS instance_system_metadata_instance_uuid \nFROM instance_system_metadata \nWHERE instance_system_metadata.instance_uuid IN ('eb216147-8e56-4b6b-99cf-bd6436fd65bb', '62e96b06-461a-4cf0-b9d5-80b981760c26', '5395b5fb-4d3e-4606-9ac4-145431f1fe93', '6fed903f-e4e5-415c-a41c-fc50bdde11de', '7fbac52f-3ee5-4c38-a25a-c52ac39c8bb7', 'e1820f1d-ef1b-4155-83fc-b5c9d782a67a', 'd6e79a50-82c0-49be-9967-2d5da9c87001', 'ade24b16-e170-4c2f-a8bd-e0b3ef60a87d', '44615531-d94b-4ff9

In [73]:
sum_of_tables = 0
sum_of_joins = 0
num_of_queries = 0
map ={}
for ele in unique_sql:
    try:
            number_of_tables = len(Parser(ele).tables)
            number_of_joins = ele.count("JOIN")
            print(str(num_of_queries)+ ":"+str(number_of_joins)+":"+str(number_of_tables))
            sum_of_tables += number_of_tables
            sum_of_joins += number_of_joins
            num_of_queries += 1
            if str(number_of_tables) in map.keys():
                map[str(number_of_tables)] += 1
            else:
                map[str(number_of_tables)] = 1
    except Exception as e:
            print(e)

0:0:1
1:0:1
2:0:1
3:0:1
4:0:1
5:0:1
6:0:1
7:0:1
8:0:1
9:3:4
10:0:1
11:13:12
12:3:4
13:0:1
14:0:1
15:0:1
16:1:2
17:1:2
18:0:1
19:0:1
20:9:8
21:0:1
22:4:5
23:0:1
24:7:4
25:0:1
26:0:1
27:0:1
28:0:1
29:2:3
30:0:1
31:7:4
32:6:7
33:3:4
34:0:1
35:0:1
36:0:1
37:0:1
38:0:1
39:0:1
40:0:1
41:7:4
42:4:5
43:0:1
44:0:1
45:0:1
46:0:1
47:0:1
48:0:1
49:0:1
50:0:1
51:0:1
52:11:10
53:0:1
54:0:1
55:0:1
56:0:1
57:9:8
58:1:2
59:0:1
60:0:1
61:3:4
62:13:12
63:0:1
64:0:1
65:0:1
66:0:1
67:0:1
68:12:12
69:0:1
70:0:1
71:0:1
72:0:1
73:0:1
74:0:1
75:0:1
76:0:1
77:0:1
78:0:1
79:0:1
80:0:1
81:0:1
82:0:1
83:3:4
84:0:1
85:13:12
86:0:1
87:0:1
88:0:1
89:0:1
90:0:1
91:6:7
92:0:1
93:0:1
94:0:1
95:0:1
96:0:1
97:0:1
98:0:1
99:0:1
100:0:1
101:0:1
102:0:1
103:0:1
104:0:1
105:0:1
106:0:1
107:0:1
108:0:1
109:0:1
110:12:12
111:0:1
112:12:11
113:0:1
114:0:1
115:0:1
116:0:1
117:0:1
118:7:4
119:0:1
120:0:1
121:0:1
122:0:1
123:0:1
124:0:1
125:6:7
126:1:2
127:0:1
128:0:1
129:0:1
130:7:4
131:0:1
132:0:1
133:0:1
134:0:1
135:2:3
136:0:1


In [74]:
sum_of_tables/num_of_queries

1.8775322283609577

In [75]:
num_of_queries

1086

In [76]:
for i in range(1, 13):
    print("number of tables in a query " + str(i) + " and they occured " + str(map[str(i)]) + " times")

number of tables in a query 1 and they occured 893 times
number of tables in a query 2 and they occured 26 times
number of tables in a query 3 and they occured 27 times
number of tables in a query 4 and they occured 62 times
number of tables in a query 5 and they occured 8 times
number of tables in a query 6 and they occured 1 times
number of tables in a query 7 and they occured 13 times
number of tables in a query 8 and they occured 4 times
number of tables in a query 9 and they occured 3 times
number of tables in a query 10 and they occured 9 times
number of tables in a query 11 and they occured 1 times
number of tables in a query 12 and they occured 39 times


In [77]:
def count_queries(df, category):
    if category == 'selection': 
        m = [my_string.count('SELECT') for my_string in df['query']]
    elif category == 'filtering': 
        m = [len(re.findall(r'^(?=.*(WHERE|HAVING)(?=.*(=|>|<|IN|BETWEEN|AND|OR|NOT|LIKE)))', my_string)) for my_string in df['query']]
    elif category == 'aggregation': 
        m = [len(re.findall(r'SUM|AVG|MAX|MIN', my_string)) for my_string in df['query']]
    elif category == 'counting': 
        m = [my_string.count('COUNT') for my_string in df['query']]
    elif category == 'grouping':
        m = [my_string.count('GROUP BY') for my_string in df['query']]
    elif category == 'ordering': 
        m = [my_string.count('ORDER BY') for my_string in df['query']]
    elif category ==  'top-k': 
        m = [len(re.findall(r'^(?=.*ORDER BY )(?=.*LIMIT )', my_string)) for my_string in df['query']]
    elif category == 'join':
        m = [my_string.count('JOIN') for my_string in df['query']]
    elif category == 'intersect': 
        m = [my_string.count('INTERSECT') for my_string in df['query']]
    elif category == 'union': 
        m = [my_string.count('UNION') for my_string in df['query']]
    elif category == 'distinct': 
        m = [my_string.count('DISTINCT') for my_string in df['query']]
    elif category == 'pattern_matching': 
        m = [my_string.count('LIKE') for my_string in df['query']]
    elif category == 'nested':
        m = [len(re.findall(r'^(?=.*SELECT.*\(SELECT)', my_string)) for my_string in df['query']]
    else: 
        print('Invalid category!')
        
    return (sum(m), max(m))

In [78]:

query_category = ['selection', 'filtering', 'aggregation', 'counting','grouping', 
                  'ordering', 'top-k', 'join', 'intersect', 'union', 'distinct', 
                  'pattern_matching', 'nested']
df = pd.DataFrame(data={'query': list(unique_sql)})
for c in query_category:
    print(c + ':')
    print(count_queries(df, c)) 
print('______________')

selection:
(946, 4)
filtering:
(246, 1)
aggregation:
(0, 0)
counting:
(0, 0)
grouping:
(51, 3)
ordering:
(61, 2)
top-k:
(0, 0)
join:
(1103, 13)
intersect:
(0, 0)
union:
(0, 0)
distinct:
(9, 1)
pattern_matching:
(1, 1)
nested:
(0, 0)
______________


In [80]:
1103/1086

1.0156537753222836

In [19]:
array = []
for a in ar:
    print(a)
    print('---')
    array.append('SELECT' + a.split(',0,,')[0])

yy,mm,dd,hh,mi,ss,seq,theTime,logID,clientIP,requestor,server,dbname,access,elapsed,busy,rows,statement,error,errorMessage,isvisible
2024,4,23,19,2,45,2900928340,2024-04-23 19:02:45.157000000,2181,172.23.55.1,preprod.skyserver.sdss.org,sdss4j,BestDR17,SkyserverWS.SearchTools.RadialSearch,7.0000002E-3,0,10
---
 TOP 10 p.objid,
 p.run, p.rerun, p.camcol, p.field, p.obj,
 p.type, p.ra, p.dec, p.u,p.g,p.r,p.i,p.z,
 p.Err_u, p.Err_g, p.Err_r,p.Err_i,p.Err_z
 FROM fGetNearbyObjEq(258.25,64.05,3) n, PhotoPrimary p
 WHERE n.objID=p.objID ,0,,1
2024,4,23,19,2,45,2900928043,2024-04-23 19:02:45.157000000,2179,172.23.55.1,preprod.skyserver.sdss.org,sdss4j,BestDR17,SkyserverWS.SearchTools.RadialSearch,7.0000002E-3,0,10
---
 TOP 10 p.objid,
 p.run, p.rerun, p.camcol, p.field, p.obj,
 p.type, p.ra, p.dec, p.u,p.g,p.r,p.i,p.z,
 p.Err_u, p.Err_g, p.Err_r,p.Err_i,p.Err_z
 FROM fGetNearbyObjEq(258.25,64.05,3) n, PhotoPrimary p
 WHERE n.objID=p.objID ,0,,1
2024,4,23,19,2,35,2900925440,2024-04-23 19:02:35.

In [20]:
array

['SELECTyy,mm,dd,hh,mi,ss,seq,theTime,logID,clientIP,requestor,server,dbname,access,elapsed,busy,rows,statement,error,errorMessage,isvisible\n2024,4,23,19,2,45,2900928340,2024-04-23 19:02:45.157000000,2181,172.23.55.1,preprod.skyserver.sdss.org,sdss4j,BestDR17,SkyserverWS.SearchTools.RadialSearch,7.0000002E-3,0,10',
 'SELECT TOP 10 p.objid,\n p.run, p.rerun, p.camcol, p.field, p.obj,\n p.type, p.ra, p.dec, p.u,p.g,p.r,p.i,p.z,\n p.Err_u, p.Err_g, p.Err_r,p.Err_i,p.Err_z\n FROM fGetNearbyObjEq(258.25,64.05,3) n, PhotoPrimary p\n WHERE n.objID=p.objID ',
 'SELECT TOP 10 p.objid,\n p.run, p.rerun, p.camcol, p.field, p.obj,\n p.type, p.ra, p.dec, p.u,p.g,p.r,p.i,p.z,\n p.Err_u, p.Err_g, p.Err_r,p.Err_i,p.Err_z\n FROM fGetNearbyObjEq(258.25,64.05,3) n, PhotoPrimary p\n WHERE n.objID=p.objID ',
 'SELECT u, r FROM PhotoObj WHERE objID = 1237667782831703006',
 'SELECT TOP 10 p.objid,\n p.run, p.rerun, p.camcol, p.field, p.obj,\n p.type, p.ra, p.dec, p.u,p.g,p.r,p.i,p.z,\n p.Err_u, p.Err_g, p.E

In [ ]:
with open(str(prefix) + '/data/SQLLogAll_Part_aa', 'r') as file:
    contents = file.read()
    print(contents[:100])

In [3]:
df_temp = pd.read_json((str(prefix) + '/data/63_queries_combined.json'))

In [4]:
df_temp

question  \
0               How many organisation units in human resources are relabeled?   
1   How many organisation units in human resources are new and not relabeled?   
2                     COUNT the number of courses offered by each department.   
3                           What are the past, upcoming, and current courses?   
4                            Which faculty has had the most location changes?   
..                                                                        ...   
57                                                     How old is a building?   
58                          How much square footage does everything supervise   
59             What year had the biggest year over year increase in building?   
60     What percent of courses have submitted TIP data for a given term code?   
61                       What kind of questions can I ask the data warehoues?   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        

In [5]:
df = df_temp['question']
db_id = []
query = []
query_toks = []
groupBy = []
question_toks = []
having = []
orderBy = []
having = []
limit = None
intersect = None
union = None
except_ = None
for i in range(len(df_temp)):
    db_id.append('mit_datawarehouse')
    query.append(df_temp['sql'][i])
    query_toks.append(df_temp['sql'][i].split(' '))
    question_toks.append(df_temp['question'][i].split(' '))

In [8]:
tables = []
for i in range(len(df_temp)):
    q = df_temp['sql'][i].upper().replace('WAREUSER.', '')
    t = Parser(q).tables
    tables.append(t)
unique_tables = set()
for t in tables: 
    for t_ in t:
        unique_tables.add(t_.upper())
unique_tables

{'ACADEMIC_TERMS',
 'ACADEMIC_TERMS_ALL',
 'ALL_VIEWS',
 'CIS_COURSE_CATALOG',
 'COURSE_CATALOG_SUBJECT_OFFERED',
 'DRUPAL_EMPLOYEE_DIRECTORY',
 'EMPLOYEE_DIRECTORY',
 'FAC_BUILDING',
 'FAC_BUILDING_ADDRESS',
 'FAC_ORGANIZATION',
 'FAC_ROOMS',
 'FCLT_BUILDING',
 'FCLT_BUILDING_ADDRESS_HIST',
 'FCLT_BUILDING_HIST',
 'FCLT_MAJOR_USE',
 'FCLT_ROOMS',
 'FIELDS',
 'HR_ORG_UNIT',
 'HR_ORG_UNIT_NEW',
 'IAP_SUBJECT_CATEGORY',
 'IAP_SUBJECT_DETAIL',
 'IAP_SUBJECT_PERSON',
 'IAP_SUBJECT_SESSION',
 'LIBRARY_COURSE_INSTRUCTOR',
 'LIBRARY_MATERIAL_STATUS',
 'LIBRARY_RESERVE_CATALOG',
 'LIBRARY_RESERVE_MATRL_DETAIL',
 'LIBRARY_SUBJECT_OFFERED',
 'MIT_STUDENT_DIRECTORY',
 'SE_PERSON',
 'SPACE_DETAIL',
 'SPACE_SUPERVISOR_USAGE',
 'STAR',
 'STAR_USER_VIEW',
 'STUDENT_DEPARTMENT',
 'SUBJECT_ENROLLABLE',
 'SUBJECT_OFFERED',
 'SUBJECT_SUMMARY',
 'TIP_DETAIL',
 'TIP_MATERIAL',
 'TIP_MATERIAL_STATUS',
 'TIP_SUBJECT_OFFERED',
 'TOP_LEVEL_DOMAIN',
 'USER_VIEW',
 'ZIP_CANADA',
 'ZIP_USA'}

In [9]:
len(unique_tables)

46

In [20]:
def open_table_schema(t:str):
    schema_file= str(prefix) + '/data/views/schema_new/' + t + '.csv'
    p = None
    if os.path.isfile(schema_file):
        return pd.read_csv(schema_file)
        #print(list(df_t_['COLUMN_NAME']))

In [18]:
columne_names = [[-1, '*']]
#column_names_original
column_types = []
db_id = 'mit_datawarehouse'
#foreign_keys
#primary_keys
table_names = list(unique_tables)
table_names_original = list(unique_tables)

In [41]:
for i in range(len(table_names)):
    df_t = open_table_schema(table_names[i])
    print(table_names[i])
    for column in df_t['COLUMN_NAME']:
        ar = [i, column]
        print(ar)
        columne_names.append(ar)
    for type in df_t['DATA_TYPE']:
        column_types.append(type)

FAC_ORGANIZATION
[0, 'ORGANIZATION_KEY']
[0, 'ORGANIZATION_ID']
[0, 'ORGANIZATION']
[0, 'ORGANIZATION_NAME']
[0, 'ORG_PARENT_KEY']
[0, 'ORG_PARENT']
[0, 'MAJOR_ORG_KEY']
[0, 'MAJOR_ORG']
[0, 'ORGANIZATION_LEVEL']
[0, 'ORGANIZATION_NUMBER']
[0, 'ORGANIZATION_SORT']
[0, 'ASSIGNABLE']
[0, 'COURSE']
[0, 'DESCRIPTION']
[0, 'WAREHOUSE_LOAD_DATE']
[0, 'D_CODE']
[0, 'HR_DEPARTMENT_CODE_OLD']
[0, 'HR_ORG_UNIT_ID']
[0, 'HR_DEPARTMENT_NAME']
FCLT_BUILDING
[1, 'FCLT_BUILDING_KEY']
[1, 'BUILDING_NUMBER']
[1, 'PARENT_BUILDING_NUMBER']
[1, 'PARENT_BUILDING_NAME']
[1, 'PARENT_BUILDING_NAME_LONG']
[1, 'BUILDING_NAME_LONG']
[1, 'EXT_GROSS_AREA']
[1, 'ASSIGNABLE_AREA']
[1, 'NON_ASSIGNABLE_AREA']
[1, 'SITE']
[1, 'CAMPUS_SECTOR']
[1, 'ACCESS_LEVEL_CODE']
[1, 'ACCESS_LEVEL_NAME']
[1, 'BUILDING_TYPE']
[1, 'OWNERSHIP_TYPE']
[1, 'BUILDING_USE']
[1, 'OCCUPANCY_CLASS']
[1, 'BUILDING_HEIGHT']
[1, 'COST_CENTER_CODE']
[1, 'COST_COLLECTOR_KEY']
[1, 'LATITUDE_WGS']
[1, 'LONGITUDE_WGS']
[1, 'EASTING_X_SPCS']
[1, 'NORT

In [23]:
column_types

['VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'DATE',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'VARCHAR2',
 'VARCHAR2',
 'NUMBER',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'DATE',
 'NUMBER',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'DATE',
 'VARCHAR2',
 'NUMBER',
 'VARCHAR2',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'NUMBER',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',
 'VARCHAR2',

In [54]:
keys = []
primary_keys = []
tabs = []
cnt = 0
foreign_keys = []
last_added_key = 0
for i, j in enumerate(columne_names):
    if j[0] - last_added_key > 1:
        cnt += 1
        last_added_key = j[0] -1
        print('_________')
        print('NOTFOUND:' + str(last_added_key))
        print(table_names[cnt-1])
        print('_________')
    if 'KEY' in j[1] or 'MIT_ID' == j[1]or 'ZIP_CODE' == j[1]or 'VIEW_ID' == j[1]or 'DEPARTMENT_CODE' == j[1]or 'SUBJECT_ID' == j[1]or 'STAR_ID' == j[1]:
        if j[0] in keys:
            print('    ' + str(i))
            print('    ' + str(j))
            print('    _________')
            foreign_keys.append([i, j[1]])
        else:
            tabs.append(j[0])
            last_added_key = j[0]
            
            print(i)
            print(j)
            keys.append(j[0])
            primary_keys.append([i, j[1]])
            if table_names[cnt] in j[1]:
                print(True)
            else:
                print('WAAAAAAAAAAAAAAAAAAAARNIng')
            print(table_names[cnt])
            print('_________')
            cnt+=1
            

1
[0, 'ORGANIZATION_KEY']
WAAAAAAAAAAAAAAAAAAAARNIng
FAC_ORGANIZATION
_________
    5
    [0, 'ORG_PARENT_KEY']
    _________
    7
    [0, 'MAJOR_ORG_KEY']
    _________
20
[1, 'FCLT_BUILDING_KEY']
True
FCLT_BUILDING
_________
    39
    [1, 'COST_COLLECTOR_KEY']
    _________
52
[2, 'TIP_MATERIAL_STATUS_KEY']
True
TIP_MATERIAL_STATUS
_________
56
[3, 'MIT_ID']
WAAAAAAAAAAAAAAAAAAAARNIng
SPACE_SUPERVISOR_USAGE
_________
65
[4, 'TIP_MATERIAL_KEY']
True
TIP_MATERIAL
_________
77
[5, 'HR_ORG_UNIT_KEY']
True
HR_ORG_UNIT
_________
    111
    [5, 'DLC_KEY']
    _________
114
[6, 'DEPARTMENT_CODE']
WAAAAAAAAAAAAAAAAAAAARNIng
STUDENT_DEPARTMENT
_________
119
[7, 'FCLT_BUILDING_HIST_KEY']
True
FCLT_BUILDING_HIST
_________
    121
    [7, 'FCLT_BUILDING_KEY']
    _________
    140
    [7, 'COST_COLLECTOR_KEY']
    _________
155
[8, 'ZIP_CODE']
WAAAAAAAAAAAAAAAAAAAARNIng
ZIP_USA
_________
161
[9, 'ACADEMIC_TERMS_KEY']
WAAAAAAAAAAAAAAAAAAAARNIng
ACADEMIC_TERMS_ALL
_________
_________
NOTFOUND:10

In [44]:
#for a in columne_names:
#    if a[0] == 5:
#        print(a)
table_names

['FAC_ORGANIZATION',
 'FCLT_BUILDING',
 'TIP_MATERIAL_STATUS',
 'SPACE_SUPERVISOR_USAGE',
 'TIP_MATERIAL',
 'HR_ORG_UNIT',
 'STUDENT_DEPARTMENT',
 'FCLT_BUILDING_HIST',
 'ZIP_USA',
 'ACADEMIC_TERMS_ALL',
 'ALL_VIEWS',
 'DRUPAL_EMPLOYEE_DIRECTORY',
 'IAP_SUBJECT_CATEGORY',
 'IAP_SUBJECT_PERSON',
 'HR_ORG_UNIT_NEW',
 'FAC_BUILDING_ADDRESS',
 'STAR_USER_VIEW',
 'SUBJECT_ENROLLABLE',
 'LIBRARY_SUBJECT_OFFERED',
 'EMPLOYEE_DIRECTORY',
 'LIBRARY_COURSE_INSTRUCTOR',
 'USER_VIEW',
 'FAC_BUILDING',
 'TIP_SUBJECT_OFFERED',
 'IAP_SUBJECT_DETAIL',
 'ACADEMIC_TERMS',
 'STAR',
 'COURSE_CATALOG_SUBJECT_OFFERED',
 'SUBJECT_OFFERED',
 'FAC_ROOMS',
 'CIS_COURSE_CATALOG',
 'TOP_LEVEL_DOMAIN',
 'IAP_SUBJECT_SESSION',
 'LIBRARY_RESERVE_MATRL_DETAIL',
 'SUBJECT_SUMMARY',
 'FCLT_BUILDING_ADDRESS_HIST',
 'FIELDS',
 'ZIP_CANADA',
 'LIBRARY_RESERVE_CATALOG',
 'TIP_DETAIL',
 'SE_PERSON',
 'FCLT_ROOMS',
 'MIT_STUDENT_DIRECTORY',
 'SPACE_DETAIL',
 'FCLT_MAJOR_USE',
 'LIBRARY_MATERIAL_STATUS']

In [55]:
primary_keys

[[1, 'ORGANIZATION_KEY'],
 [20, 'FCLT_BUILDING_KEY'],
 [52, 'TIP_MATERIAL_STATUS_KEY'],
 [56, 'MIT_ID'],
 [65, 'TIP_MATERIAL_KEY'],
 [77, 'HR_ORG_UNIT_KEY'],
 [114, 'DEPARTMENT_CODE'],
 [119, 'FCLT_BUILDING_HIST_KEY'],
 [155, 'ZIP_CODE'],
 [161, 'ACADEMIC_TERMS_KEY'],
 [192, 'MIT_ID'],
 [210, 'IAP_SUBJECT_CATEGORY_KEY'],
 [214, 'IAP_SUBJECT_PERSON_KEY'],
 [223, 'HR_ORG_UNIT_KEY'],
 [254, 'BUILDING_ADDRESS_KEY'],
 [268, 'STAR_ID'],
 [271, 'SUBJECT_ID'],
 [281, 'LIBRARY_SUBJECT_OFFERED_KEY'],
 [301, 'MIT_ID'],
 [322, 'LIBRARY_COURSE_INSTRUCTOR_KEY'],
 [331, 'VIEW_ID'],
 [343, 'FAC_BUILDING_KEY'],
 [371, 'TIP_SUBJECT_OFFERED_KEY'],
 [392, 'IAP_SUBJECT_CATEGORY_KEY'],
 [411, 'ACADEMIC_TERMS_KEY'],
 [435, 'STAR_ID'],
 [442, 'SUBJECT_ID'],
 [509, 'SUBJECT_KEY'],
 [557, 'FAC_ROOM_KEY'],
 [598, 'SUBJECT_ID'],
 [639, 'TOP_LEVEL_DOMAIN_KEY'],
 [643, 'IAP_SUBJECT_SESSION_KEY'],
 [653, 'LIBRARY_COURSE_INSTRUCTOR_KEY'],
 [660, 'SUBJECT_SUMMARY_KEY'],
 [701, 'FCLT_BUILDING_ADDRESS_KEY'],
 [719, 'TAB

In [56]:
foreign = []
for ar in primary_keys:
    for ar2 in foreign_keys:
        if ar[1]==ar2[1]:
            foreign.append([ar2[0], ar[0]])

In [57]:
foreign


[[569, 1],
 [822, 1],
 [1390, 1],
 [1643, 1],
 [2211, 1],
 [121, 20],
 [702, 20],
 [766, 20],
 [841, 20],
 [942, 20],
 [1523, 20],
 [1587, 20],
 [1662, 20],
 [1763, 20],
 [2344, 20],
 [2408, 20],
 [746, 52],
 [873, 52],
 [1567, 52],
 [1694, 52],
 [2388, 52],
 [877, 56],
 [1013, 56],
 [1122, 56],
 [1573, 56],
 [1698, 56],
 [1834, 56],
 [1943, 56],
 [2394, 56],
 [745, 65],
 [886, 65],
 [1566, 65],
 [1707, 65],
 [2387, 65],
 [898, 77],
 [1044, 77],
 [1719, 77],
 [1865, 77],
 [448, 114],
 [604, 114],
 [672, 114],
 [935, 114],
 [1269, 114],
 [1425, 114],
 [1493, 114],
 [1756, 114],
 [2090, 114],
 [2246, 114],
 [2314, 114],
 [940, 119],
 [1761, 119],
 [976, 155],
 [1797, 155],
 [982, 161],
 [1232, 161],
 [1803, 161],
 [2053, 161],
 [877, 192],
 [1013, 192],
 [1122, 192],
 [1573, 192],
 [1698, 192],
 [1834, 192],
 [1943, 192],
 [2394, 192],
 [1031, 210],
 [1213, 210],
 [1852, 210],
 [2034, 210],
 [395, 214],
 [1035, 214],
 [1216, 214],
 [1856, 214],
 [2037, 214],
 [898, 223],
 [1044, 223],
 [

In [1]:

import torch
torch.cuda.empty_cache()
%run ../scripts/rag.py


2024-04-25 17:40:17.663467: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-04-25 17:40:17.663506: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-04-25 17:40:17.664778: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-04-25 17:40:17.671108: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-04-25 17:40:18.470574: W tensorflow/compiler/tf2

/home/skikk/Dokumente/uni/WS2324/MIT/llm-enterprise
['How many organisation units in human resources are relabeled?', 'How many organisation units in human resources are new and not relabeled?', 'Count the number of courses offered by each department.', 'What are the past, upcoming, and current courses?', 'Which faculty has had the most location changes?', 'What is the average number of courses a student can enroll in?', 'Which students are employed by mit?', 'What is the shortest course available this semester?', 'Show buildings and their address.', 'How many students do we have?', 'Show all statuses for materials?', 'What are the different cities where people live?', 'Give the average number of courses in one department with more than 100 courses.', 'Count the number of room in a building.', 'Count the number of space-units per building.', 'For courses that have descriptions of Regular and Initial, what are their start dates?', 'What are the names of the 3 departments which offer the

INFO:AnglE:Prompt is set, the prompt will be automatically applied during the encoding phase. To disable prompt setting, please configure set_prompt(prompt=None)


Represent this sentence for searching relevant passages: {text}


  0%|                                                                                                      | 0/1 [00:02<?, ?it/s]


OutOfMemoryError: CUDA out of memory. Tried to allocate 166.00 MiB. GPU 